In [15]:
import pywikibot
import mwparserfromhell
import re
import pandas as pd

from collections import defaultdict
from sklearn import preprocessing
from pywikibot import pagegenerators

### Scrape Wikipedia

In [65]:
# The language code for the wiki you want to access; connect to site
wiki_language = "en"
site = pywikibot.Site(wiki_language, "wikipedia")

# Initiate graph traversing with some beginning article
source_page = pywikibot.Page(site, "Philosophy")

# Initiate graph traversal variables
visited = []
queue = []
#visited.append(source_page.title())
#queue.append(source_page.title())
visited.append(source_page)
queue.append(source_page)

# Initiate data gathering variables
# For nodes
pop_count = 0

# For links
sources = []
targets = []

# For node info
node_names = []
node_summaries = []
node_et_equivalent = []

def get_content(site, node_page):
    print("Getting content of page:", node_page)
    try:
        #node_page = pywikibot.Page(site, node_title)
        page_content = mwparserfromhell.parse(node_page.get()).strip_code()
        return page_content
    except pywikibot.exceptions.Error as e:
        print(e)
        return None

def parse_content_and_get_other_langlinks(node_page, page_content):
    page_content = page_content.replace("\n", " ").replace(u'\xa0', u' ')
    page_content = ". ".join(page_content[:500].split(". "[:-1])) + "."
    other_lang_links = defaultdict(None, {langlink.site.lang: langlink.title for langlink in node_page.langlinks()})
    return page_content, other_lang_links
    
def remember_node_attributes(node_page, page_content, other_lang_links):
    node_names.append(node_page.title())
    node_summaries.append(page_content)
    node_et_equivalent.append(other_lang_links.get("et"))
    return

while queue:
    node_page = queue.pop(0)
    pop_count += 1
    
    print(pop_count, node_page)
    
    # Get current node's article for its attributes and links
    page_content = get_content(site, node_page)
    if page_content == None:
        pop_count -= 1
        continue
        
    # Only has to be done once for the init node, because linked pages will be retrieved in batches and with content
    if pop_count == 1:
        page_content, other_lang_links = parse_content_and_get_other_langlinks(node_page, page_content)
        remember_node_attributes(node_page, page_content, other_lang_links)
    
    print("Retrieving links from page:", node_page)
    linked_pages = list(pagegenerators.LinkedPageGenerator(node_page, content=True))
    print("Retrieved", len(linked_pages), "pages")
    for linked_page in linked_pages:
        linked_page_title = linked_page.title()
        
        # For data 
        # Links between nodes have to be gathered multiple times, as they can exist multiple times
        sources.append(node_page.title())
        targets.append(linked_page_title)
        
        # Get current node's article for its attributes and links
        page_content = get_content(site, linked_page)
        if page_content == None:
            continue
            
        # TODO: These next two lines should probably be in the next if clause
        # but alternatively duplicate nodes can just be dropped afterwards
        linked_page_content, linked_other_lang_links = parse_content_and_get_other_langlinks(linked_page, page_content)
        remember_node_attributes(linked_page, linked_page_content, linked_other_lang_links)
        
        # Continue BFS until we have 100 nodes with their immediate neighbours (that's gonna be a lot more nodes than just 100)
        if linked_page_title not in visited and len(visited) < 100:
            # For traversing
            visited.append(linked_page)
            queue.append(linked_page)

1 [[en:Philosophy]]
Getting content of page: [[en:Philosophy]]
Retrieving links from page: [[en:Philosophy]]
Retrieved 929 pages
Getting content of page: [[en:19th-century philosophy]]
Getting content of page: [[en:A posteriori knowledge]]
Page [[en:A posteriori knowledge]] is a redirect page.
Getting content of page: [[en:A priori knowledge]]
Page [[en:A priori knowledge]] is a redirect page.
Getting content of page: [[en:Abhidharma]]
Getting content of page: [[en:Absolute idealism]]
Getting content of page: [[en:Abstract object]]
Page [[en:Abstract object]] is a redirect page.
Getting content of page: [[en:Academic Skepticism]]
Page [[en:Academic Skepticism]] is a redirect page.
Getting content of page: [[en:Academic skepticism]]
Getting content of page: [[en:Accident (philosophy)]]
Getting content of page: [[en:Achintya Bheda Abheda]]
Getting content of page: [[en:Action (philosophy)]]
Getting content of page: [[en:Action theory (philosophy)]]
Getting content of page: [[en:Adharma]]

Getting content of page: [[en:Confucius]]
Getting content of page: [[en:Consequent]]
Getting content of page: [[en:Consequentialism]]
Getting content of page: [[en:Conservatism]]
Getting content of page: [[en:Contemporary Islamic philosophy]]
Getting content of page: [[en:Contemporary Western philosophy]]
Page [[en:Contemporary Western philosophy]] is a redirect page.
Getting content of page: [[en:Contemporary philosophy]]
Getting content of page: [[en:Continental philosophy]]
Getting content of page: [[en:Coricancha]]
Getting content of page: [[en:Cosmology]]
Getting content of page: [[en:Counterfactual thinking]]
Getting content of page: [[en:Creator deity]]
Getting content of page: [[en:Critical race theory]]
Getting content of page: [[en:Critical rationalism]]
Getting content of page: [[en:Critical theory]]
Getting content of page: [[en:Cubist]]
Page [[en:Cubist]] is a redirect page.
Getting content of page: [[en:Curlie]]
Page [[en:Curlie]] is a redirect page.
Getting content of pa

Getting content of page: [[en:Helmut Thielicke]]
Getting content of page: [[en:Henry Corbin]]
Getting content of page: [[en:Hermeneutics]]
Getting content of page: [[en:Hindu]]
Page [[en:Hindu]] is a redirect page.
Getting content of page: [[en:Hindu philosophy]]
Getting content of page: [[en:Hinduism]]
Getting content of page: [[en:Hipparchia of Maroneia]]
Getting content of page: [[en:Historical Vedic religion]]
Getting content of page: [[en:Historicism]]
Getting content of page: [[en:History]]
Getting content of page: [[en:History of China]]
Getting content of page: [[en:History of Hinduism]]
Getting content of page: [[en:History of philosophy]]
Page [[en:History of philosophy]] is a redirect page.
Getting content of page: [[en:History of philosophy in Poland]]
Getting content of page: [[en:Holism]]
Getting content of page: [[en:Hu Shih]]
Getting content of page: [[en:Human body]]
Getting content of page: [[en:Humanism]]
Getting content of page: [[en:Humanistic Buddhism]]
Getting co

Getting content of page: [[en:Logos]]
Getting content of page: [[en:Luciano Floridi]]
Getting content of page: [[en:Ludwig Wittgenstein]]
Getting content of page: [[en:Madhyamaka]]
Getting content of page: [[en:Magadha]]
Getting content of page: [[en:Mahasi Sayadaw]]
Getting content of page: [[en:Mahayana]]
Getting content of page: [[en:Mahāsāṃghika]]
Getting content of page: [[en:Maimonides]]
Getting content of page: [[en:Manichaeism]]
Getting content of page: [[en:Mao Zedong]]
Getting content of page: [[en:Marc Van de Mieroop]]
Getting content of page: [[en:Martha Nussbaum]]
Getting content of page: [[en:Martin Heidegger]]
Getting content of page: [[en:Martín de Murúa]]
Getting content of page: [[en:Marxism]]
Getting content of page: [[en:Marxist philosophy]]
Getting content of page: [[en:Mary Wollstonecraft]]
Getting content of page: [[en:Materialism]]
Getting content of page: [[en:Mathematical logic]]
Getting content of page: [[en:Mathematics]]
Getting content of page: [[en:Mazdaki

Getting content of page: [[en:Philosophy of Friedrich Nietzsche]]
Getting content of page: [[en:Philosophy of Søren Kierkegaard]]
Getting content of page: [[en:Philosophy of biology]]
Getting content of page: [[en:Philosophy of history]]
Getting content of page: [[en:Philosophy of language]]
Getting content of page: [[en:Philosophy of mathematics]]
Getting content of page: [[en:Philosophy of mind]]
Getting content of page: [[en:Philosophy of religion]]
Getting content of page: [[en:Philosophy of science]]
Getting content of page: [[en:Philosophy of space and time]]
Getting content of page: [[en:Physicalism]]
Getting content of page: [[en:Physics]]
Getting content of page: [[en:Physics (Aristotle)]]
Getting content of page: [[en:Plato]]
Getting content of page: [[en:Platonic Academy]]
Getting content of page: [[en:Platonism]]
Getting content of page: [[en:Political philosophy]]
Getting content of page: [[en:Politics]]
Getting content of page: [[en:Pope John Paul II]]
Getting content of 

...

Getting content of page: [[en:Neo-scholasticism]]
Getting content of page: [[en:Neoplatonism]]
Getting content of page: [[en:Neopythagoreanism]]
Getting content of page: [[en:Nettipakarana]]
Page [[en:Nettipakarana]] is a redirect page.
Getting content of page: [[en:Neville Karunatilake]]
Getting content of page: [[en:New Confucianism]]
Getting content of page: [[en:New York City]]
Getting content of page: [[en:New historicism]]
Getting content of page: [[en:Newar Buddhism]]
Getting content of page: [[en:Newtonianism]]
Getting content of page: [[en:Ngok Loden Sherab]]
Getting content of page: [[en:Nianfo]]
Getting content of page: [[en:Nichiren]]
Getting content of page: [[en:Nichiren Buddhism]]
Getting content of page: [[en:Nididhyasana]]
Page [[en:Nididhyasana]] is a redirect page.
Getting content of page: [[en:Nihilism]]
Getting content of page: [[en:Nikayas]]
Page [[en:Nikayas]] is a redirect page.
Getting content of page: [[en:Nimbarka Sampradaya]]
Getting content of page: [[en:Ni

Getting content of page: [[en:Process philosophy]]
Getting content of page: [[en:Progressive utilization theory]]
Getting content of page: [[en:Prostration (Buddhism)]]
Getting content of page: [[en:Prātimokṣa]]
Page [[en:Prātimokṣa]] is a redirect page.
Getting content of page: [[en:Pudgalavada]]
Getting content of page: [[en:Pudgalavadin]]
Page [[en:Pudgalavadin]] is a redirect page.
Getting content of page: [[en:Punna]]
Page [[en:Punna]] is a redirect page.
Getting content of page: [[en:Pure Land]]
Page [[en:Pure Land]] is a redirect page.
Getting content of page: [[en:Pure Land Buddhism]]
Getting content of page: [[en:Purusha]]
Getting content of page: [[en:Pyrrho]]
Getting content of page: [[en:Pyrrhonism]]
Getting content of page: [[en:Pythagoreanism]]
Getting content of page: [[en:Pāli Canon]]
Page [[en:Pāli Canon]] is a redirect page.
Getting content of page: [[en:Pāli Text Society]]
Page [[en:Pāli Text Society]] is a redirect page.
Getting content of page: [[en:Pāramitā]]
Gett

Getting content of page: [[en:Silk Road transmission of Buddhism]]
Getting content of page: [[en:Similarities between Pyrrhonism and Buddhism]]
Page [[en:Similarities between Pyrrhonism and Buddhism]] is a redirect page.
Getting content of page: [[en:Simran]]
Getting content of page: [[en:Sinhalese Buddhist nationalism]]
Getting content of page: [[en:Six realms]]
Page [[en:Six realms]] is a redirect page.
Getting content of page: [[en:Skanda (Buddhism)]]
Getting content of page: [[en:Skandha]]
Getting content of page: [[en:Skandhas]]
Page [[en:Skandhas]] is a redirect page.
Getting content of page: [[en:Social constructionism]]
Getting content of page: [[en:Social contract]]
Getting content of page: [[en:Social convention]]
Page [[en:Social convention]] is a redirect page.
Getting content of page: [[en:Social philosophy]]
Getting content of page: [[en:Socialism]]
Getting content of page: [[en:Solipsism]]
Getting content of page: [[en:Songtsen Gampo]]
Getting content of page: [[en:Sophi

Getting content of page: [[en:Vairocana]]
Getting content of page: [[en:Vaisheshika]]
Getting content of page: [[en:Vaiśeṣika Sūtra]]
Getting content of page: [[en:Vajrabodhi]]
Getting content of page: [[en:Vajrapani]]
Getting content of page: [[en:Vajrasekhara Sutra]]
Getting content of page: [[en:Vajrayana]]
Getting content of page: [[en:Valluvar]]
Page [[en:Valluvar]] is a redirect page.
Getting content of page: [[en:Vassa]]
Getting content of page: [[en:Vasubandhu]]
Getting content of page: [[en:Vedana]]
Page [[en:Vedana]] is a redirect page.
Getting content of page: [[en:Vedanga]]
Getting content of page: [[en:Vedanta]]
Getting content of page: [[en:Vedanta Desika]]
Getting content of page: [[en:Vedas]]
Getting content of page: [[en:Vesak]]
Getting content of page: [[en:Vibhajyavāda]]
Getting content of page: [[en:Vienna Circle]]
Getting content of page: [[en:Vietnamese Thiền]]
Page [[en:Vietnamese Thiền]] is a redirect page.
Getting content of page: [[en:Vietnamese philosophy]]
G

Getting content of page: [[en:Category:Political philosophy literature]]
Getting content of page: [[en:Category:Use dmy dates from July 2020]]
Getting content of page: [[en:Portal:Philosophy]]
Getting content of page: [[en:Portal:Religion]]


In [66]:
len(sources), len(targets)

(69149, 69149)

In [67]:
len(node_names), len(node_summaries), len(node_et_equivalent)

(60792, 60792, 60792)

In [68]:
idx = 6
node_names[idx], node_summaries[idx], node_et_equivalent[idx]

('Achintya Bheda Abheda',
 "Achintya-Bheda-Abheda (अचिन्त्यभेदाभेद,  in IAST) is a school of Vedanta representing the philosophy of inconceivable one-ness and difference. pp.  47-52 In Sanskrit achintya means 'inconceivable', bheda translates as 'difference', and abheda translates as 'non-difference'.  thumb|Chaitanya Mahaprabhu (1486–1534 CE), the founder of Achintya Bheda Abheda school and Gaudiya Vaishnavism The Gaudiya Vaishnava religious tradition employs the term in relation to the relationship of creation and creator (.",
 'Acintya-bhedābheda')

### Create nodes and edges DataFrames

In [125]:
# Create edges dataframe
edges = pd.DataFrame({"source": sources, "target": targets})

In [127]:
# Create IDs for all nodes
unique_source_nodes = set(edges.source.values)
unique_target_nodes = set(edges.target.values)
all_nodes = list(unique_source_nodes.union(unique_target_nodes))

le = preprocessing.LabelEncoder()
le.fit(all_nodes)

# Create nodes DataFrame without metadata
nodes_without_metadata = pd.DataFrame({"node_id": le.transform(all_nodes), "node_name": all_nodes})

# Create nodes DataFrame with metadata
nodes_with_metadata = pd.DataFrame({"node_id": le.transform(node_names),
                                    "node_summary": node_summaries, 
                                    "node_et_equivalent": node_et_equivalent})

nodes = nodes_without_metadata.merge(nodes_with_metadata, on="node_id", how="left")
nodes = nodes.drop_duplicates()

edges["source"] = le.transform(edges["source"])
edges["target"] = le.transform(edges["target"])

In [136]:
nodes

node_id                          node_name  \
0        27685                             Tantra   
10         911     African Americans in Tennessee   
11        3359                         Asia Minor   
12       13296        Hot in Cleveland (season 5)   
13        6720                 Christopher Duggan   
...        ...                                ...   
66186     7475              Cormac Burke (priest)   
66187    30894                      Western world   
66194    13108  History of the Hungarian language   
66195      140     1996 Nobel Prize in Literature   
66196     7636                      Crisis theory   

                                            node_summary node_et_equivalent  
0         Tantra (; ) refers to an  esoteric yogic tr...            Tantrad  
10     African Americans are the second largest ethni...               None  
11                                                   NaN                NaN  
12     The fifth season of the TV Land original sitco...               None  
13     Christopher John Hesketh Duggan (4 November 19...               None  
...                                                  ...                ...  
66186                                                NaN                NaN  
66187  The Western world, also known as the West, pri...        Läänemaailm  
66194  right|thumb|250px|The "Funeral Sermon and Pray...               None  
66195  The 1996 Nobel Prize in Literature was awarded...               None  
66196  Crisis theory, concerning the causes'The cause...               None  

[31821 rows x 4 columns]

In [137]:
edges

source  target
0       22260     150
1       22260     264
2       22260     266
3       22260     402
4       22260     460
...       ...     ...
69144    5237    6054
69145    5237    6064
69146    5237    6125
69147    5237   22836
69148    5237   22841

[69149 rows x 2 columns]

In [130]:
nodes.to_csv("nodes.csv", index=False)

In [131]:
edges.to_csv("edges.csv", index=False)